In [41]:
# %%
import pandas as pd
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt

df = pd.read_json('../data/TSXData.json')
# Sort by timestamp unix
df = df.sort_values(by=['TimeStamp'])

In [2]:
df.MessageType.unique()

array(['NewOrderRequest', 'NewOrderAcknowledged', 'CancelRequest',
       'CancelAcknowledged', 'Cancelled', 'Trade'], dtype=object)

In [3]:
df.OrderID.nunique()

44768

In [4]:
# Unique Order IDs for Trade
matches = []
for order_id in df[df.MessageType=='Trade'].OrderID.unique():
    orderfilter = df[df.OrderID==order_id]
    if orderfilter.shape[0] > 1:
        print(f'FOUND with shape {orderfilter.shape}!')
        matches.append(orderfilter)
        break

FOUND with shape (6, 8)!


### ANOMALY DETECTED

In [5]:
matches[0].head(20)

TimeStamp                TimeStampEpoch  \
53287 2023-01-06 09:30:00.238813104 2023-01-06 14:30:00.238813104   
53292 2023-01-06 09:30:00.238878716 2023-01-06 14:30:00.238878716   
53293 2023-01-06 09:30:00.238891893 2023-01-06 14:30:00.238891893   
53730 2023-01-06 09:30:00.268049672 2023-01-06 14:30:00.268049672   
53734 2023-01-06 09:30:00.268169562 2023-01-06 14:30:00.268169562   
53735 2023-01-06 09:30:00.268174478 2023-01-06 14:30:00.268174478   

           Direction                               OrderID  \
53287  ExchangeToNBF  b96e916e-9283-11ed-ac0d-047c16291a22   
53292  ExchangeToNBF  b96e916e-9283-11ed-ac0d-047c16291a22   
53293  ExchangeToNBF  b96e916e-9283-11ed-ac0d-047c16291a22   
53730  NBFToExchange  b96e916e-9283-11ed-ac0d-047c16291a22   
53734  ExchangeToNBF  b96e916e-9283-11ed-ac0d-047c16291a22   
53735  ExchangeToNBF  b96e916e-9283-11ed-ac0d-047c16291a22   

              MessageType Symbol  OrderPrice Exchange  
53287               Trade  MLW24      140.14      TSX  
53292               Trade  MLW24      140.14      TSX  
53293               Trade  MLW24      140.14      TSX  
53730       CancelRequest  MLW24         NaN      TSX  
53734  CancelAcknowledged  MLW24         NaN      TSX  
53735           Cancelled  MLW24         NaN      TSX

In [6]:
# Random Order ID
message = None
while message is None or message == 'Cancelled':
    random_transaction = df[df.OrderID==df.OrderID.sample(1).values[0]][['TimeStampEpoch', 'OrderID', 'MessageType', 'Symbol']]
    message = random_transaction['MessageType'].iloc[-1]

random_transaction.head()

TimeStampEpoch                               OrderID  \
195786 2023-01-06 14:31:44.379774918  b98f5ff8-9283-11ed-a35a-047c16291a22   
195791 2023-01-06 14:31:44.379875296  b98f5ff8-9283-11ed-a35a-047c16291a22   

                 MessageType Symbol  
195786       NewOrderRequest  WHKCN  
195791  NewOrderAcknowledged  WHKCN

In [56]:
df['RoundedTimeStamp'] = df.TimeStamp.dt.round("S")

In [57]:
df.head()

TimeStamp                TimeStampEpoch      Direction  \
0 2023-01-06 09:28:00.011058962 2023-01-06 14:28:00.011058962  NBFToExchange   
1 2023-01-06 09:28:00.011081372 2023-01-06 14:28:00.011081372  NBFToExchange   
2 2023-01-06 09:28:00.011117286 2023-01-06 14:28:00.011117286  ExchangeToNBF   
3 2023-01-06 09:28:00.011125452 2023-01-06 14:28:00.011125452  NBFToExchange   
4 2023-01-06 09:28:00.011129285 2023-01-06 14:28:00.011129285  NBFToExchange   

                                OrderID           MessageType Symbol  \
0  b963bbc8-9283-11ed-9ad4-047c16291a22       NewOrderRequest  OA14Y   
1  b963bbc9-9283-11ed-8b08-047c16291a22       NewOrderRequest  OOOTO   
2  b963bbc8-9283-11ed-9ad4-047c16291a22  NewOrderAcknowledged  OA14Y   
3  b963bbca-9283-11ed-b19f-047c16291a22         CancelRequest  OA14Y   
4  b963bbcb-9283-11ed-aba1-047c16291a22       NewOrderRequest  NQGAH   

   OrderPrice Exchange    RoundedTimeStamp  
0       61.56      TSX 2023-01-06 09:28:00  
1       69.37      TSX 2023-01-06 09:28:00  
2       61.56      TSX 2023-01-06 09:28:00  
3         NaN      TSX 2023-01-06 09:28:00  
4       73.20      TSX 2023-01-06 09:28:00

In [59]:
lower_bound = df.TimeStamp.min()
upper_bound = lower_bound + pd.Timedelta(seconds=1)

df[(df.TimeStamp >= lower_bound) & (df.TimeStamp <= upper_bound)].index

Int64Index([   0,    1,    2,    3,    4,    5,    6,    7,    8,    9,
            ...
            1470, 1471, 1472, 1473, 1474, 1475, 1476, 1477, 1478, 1479],
           dtype='int64', length=1480)

In [55]:
fig = px.violin(df[~df.OrderPrice.isna()], y='OrderPrice', x='MessageType', color='MessageType', box=False, points='outliers')
fig.show()